# Reductions in memory

In this benchmark we will compare ironArray's performance with Zarr, HDF5, Numpy and TileDB. We will work with the data used in the [Reductions tutorial](../tutorials/05.Reductions.html) with the default chunk shapes for every library and compute the same reduction for every case with in memory operands.  It is important to stress that we are using defaults for every library, which are typically fine tuned for general performance; this is a pretty fair way to compare them without spending long time optimizing for every one.


Let's go:

In [1]:
%load_ext memprofiler

import numpy as np
import iarray as ia
import os
import zarr
import dask.array as da
import h5py
import hdf5plugin as h5plugin
from numcodecs import Blosc
import tiledb

In [2]:
!du -sh ../tutorials/precip-3m.iarr

672M	../tutorials/precip-3m.iarr


## Data

In [3]:
%%time

ia_precip = ia.load("../tutorials/precip-3m.iarr")
print(ia_precip.shape)
print("cratio: ", round(ia_precip.cratio, 2))
chunks = ia_precip.chunks
print(ia_precip.info)

(3, 720, 721, 1440)
cratio:  15.43
type   : IArray
shape  : (3, 720, 721, 1440)
chunks : (1, 128, 128, 256)
blocks : (1, 16, 32, 64)
cratio : 15.43

CPU times: user 27.5 ms, sys: 712 ms, total: 739 ms
Wall time: 1.19 s


In [4]:
%%time
precip = ia_precip.data

CPU times: user 9.63 s, sys: 6.94 s, total: 16.6 s
Wall time: 14.3 s


In [5]:
precip_zarr = zarr.array(ia_precip.data)
print(precip_zarr.info)
precip_zdask = da.from_zarr(precip_zarr)

Type               : zarr.core.Array
Data type          : float32
Shape              : (3, 720, 721, 1440)
Chunk shape        : (1, 90, 91, 180)
Order              : C
Read-only          : False
Compressor         : Blosc(cname='lz4', clevel=5, shuffle=SHUFFLE, blocksize=0)
Store type         : builtins.dict
No. bytes          : 8970393600 (8.4G)
No. bytes stored   : 1117920644 (1.0G)
Storage ratio      : 8.0
Chunks initialized : 1536/1536



In [6]:
# TileDB does not come with defaults for chunk shape (tiles), so using ironArray's one
shape = ia_precip.shape
adom = tiledb.Domain(
        tiledb.Dim(name="rows", domain=(0, shape[0] - 1), dtype=np.int32, tile=chunks[0]),
        tiledb.Dim(name="cols", domain=(0, shape[1] - 1), dtype=np.int32, tile=chunks[1]),
        tiledb.Dim(name="else", domain=(0, shape[2] - 1), dtype=np.int32, tile=chunks[2]),
        tiledb.Dim(name="else2", domain=(0, shape[3] - 1), dtype=np.int32, tile=chunks[3]),
    )

filters = tiledb.FilterList([tiledb.ByteShuffleFilter(), tiledb.LZ4Filter(5)])
aschema = tiledb.ArraySchema(
    domain=adom,  sparse=False, attrs=[tiledb.Attr(name="a", dtype=np.float32, filters=filters)]
)

# Create the (empty) array on disk.
tiledb_name = "mem://precip-3m-optimal.tiledb"
if not os.path.exists(tiledb_name):
    tiledb.DenseArray.create(tiledb_name, aschema)
    with tiledb.DenseArray(tiledb_name, mode="w") as A_opt:
        A_opt[:] = ia_precip.data

dask_tiledb = da.from_tiledb(tiledb_name, attribute='a')

## Std

### ironArray

In [7]:
%%mprof_run 1.iarray::std_memory
ia_reduc = ia.std(ia_precip, axis=(3, 0)).data

memprofiler: used 504.80 MiB RAM (peak of 506.76 MiB) in 11.5608 s, total RAM usage 857.52 MiB


### NumPy

Let's do the same computation with NumPy. First we will get the NumPy array from the ironArray one:

and now the actual reduction:

In [8]:
%%mprof_run 5.numpy::std_memory
np_reduc = np.std(precip, axis=(3, 0))

memprofiler: used -815.23 MiB RAM (peak of 7269.05 MiB) in 74.6808 s, total RAM usage 42.41 MiB


In [9]:
np.testing.assert_allclose(ia_reduc, np_reduc, atol=1e-5, rtol=1e-5)
del np_reduc

### Zarr

In [10]:
%%mprof_run 2.zarr::std_memory
zdask_reduc = da.std(precip_zdask, axis=(3, 0))
zarr_reduc = zarr.create(shape=ia_reduc.shape, dtype=ia_reduc.dtype)
da.to_zarr(zdask_reduc, zarr_reduc)

memprofiler: used 1127.84 MiB RAM (peak of 6788.67 MiB) in 9.6234 s, total RAM usage 1275.66 MiB


In [11]:
np.testing.assert_almost_equal(zarr_reduc, ia_reduc)
del zdask_reduc
del zarr_reduc

### HDF5

In [12]:
h5_urlpath = "precip-3m.hdf5"

if not os.path.exists(h5_urlpath):
    with h5py.File(h5_urlpath, "w") as f:
        h5_precip = f.create_dataset("h5_precip", ia_precip.shape, dtype=ia_precip.dtype, **h5plugin.Blosc())
        ia_precip.copyto(h5_precip)


h5_file = h5py.File(h5_urlpath, "r", driver='core', backing_store=False)
precip_h5 = h5_file['h5_precip']


precip_h5dask = da.from_array(precip_h5)

h5_reduc_urlpath = "reduc.hdf5"
ia.remove_urlpath(h5_reduc_urlpath)

In [13]:
%%mprof_run 3.hdf5::std_memory

h5dask_reduc = da.std(precip_h5dask, axis=(3, 0))

f = h5py.File(h5_reduc_urlpath, "w", driver='core', backing_store=False)
h5_reduc = f.create_dataset(name=h5_reduc_urlpath, shape=ia_reduc.shape, dtype=ia_reduc.dtype, **h5plugin.Blosc())
da.to_hdf5(h5_reduc_urlpath, '/x', h5dask_reduc)
f.close()

memprofiler: used 10.37 MiB RAM (peak of 4488.48 MiB) in 16.3575 s, total RAM usage 2376.88 MiB


In [14]:
del h5dask_reduc
del h5_reduc

### TileDB

In [15]:
%%mprof_run 4.tiledb::std_memory
res_dask_opt = da.std(dask_tiledb, axis=(3, 0))
res_dask_opt.to_tiledb("mem://res_tiledb")

memprofiler: used -1415.45 MiB RAM (peak of 4681.15 MiB) in 19.5314 s, total RAM usage 961.57 MiB


In [16]:
del res_dask_opt
tiledb.remove("mem://res_tiledb")

### Results

Finally, we will do a plot of the memory and time consumption with each different library.

In [17]:
%mprof_plot .*::std

## max

### ironArray

In [18]:
%%mprof_run 1.iarray::max_memory
ia_reduc = ia.max(ia_precip, axis=(3, 0)).data

memprofiler: used 674.64 MiB RAM (peak of 675.48 MiB) in 3.5711 s, total RAM usage 1730.32 MiB


### NumPy

Let's do the same computation with NumPy. First we will get the NumPy array from the ironArray one:

and now the actual reduction:

In [19]:
%%mprof_run 5.numpy::max_memory
np_reduc = np.max(precip, axis=(3, 0))

memprofiler: used 1854.47 MiB RAM (peak of 3385.05 MiB) in 22.7873 s, total RAM usage 3584.81 MiB


In [20]:
np.testing.assert_allclose(ia_reduc, np_reduc, atol=1e-5, rtol=1e-5)
del np_reduc

### Zarr

In [21]:
%%mprof_run 2.zarr::max_memory
zdask_reduc = da.max(precip_zdask, axis=(3, 0))
zarr_reduc = zarr.create(shape=ia_reduc.shape, dtype=ia_reduc.dtype)
da.to_zarr(zdask_reduc, zarr_reduc)

memprofiler: used -1739.62 MiB RAM (peak of 309.83 MiB) in 10.3085 s, total RAM usage 1951.18 MiB


In [22]:
np.testing.assert_almost_equal(zarr_reduc, ia_reduc)
del zdask_reduc
del zarr_reduc

### HDF5

In [23]:
%%mprof_run 3.hdf5::max_memory

h5dask_reduc = da.max(precip_h5dask, axis=(3, 0))

f = h5py.File(h5_reduc_urlpath, "w", driver='core', backing_store=False)
h5_reduc = f.create_dataset(name=h5_reduc_urlpath, shape=ia_reduc.shape, dtype=ia_reduc.dtype, **h5plugin.Blosc())
da.to_hdf5(h5_reduc_urlpath, '/x', h5dask_reduc)
f.close()

memprofiler: used 855.23 MiB RAM (peak of 6076.57 MiB) in 20.2536 s, total RAM usage 2814.81 MiB


In [24]:
del h5dask_reduc
del h5_reduc

### TileDB

In [25]:
%%mprof_run 4.tiledb::max_memory
res_dask_opt = da.max(dask_tiledb, axis=(3, 0))
res_dask_opt.to_tiledb("mem://res_tiledb")

memprofiler: used 490.28 MiB RAM (peak of 5463.16 MiB) in 13.9821 s, total RAM usage 3305.45 MiB


In [26]:
del res_dask_opt
tiledb.remove("mem://res_tiledb")

### Results

Finally, we will do a plot of the memory and time consumption with each different library.

In [27]:
%mprof_plot .*::max

## median

### ironArray

In [28]:
%%mprof_run 1.iarray::median_memory
ia_reduc = ia.median(ia_precip, axis=(3, 0)).data

memprofiler: used 743.34 MiB RAM (peak of 767.64 MiB) in 14.5232 s, total RAM usage 4032.66 MiB


### NumPy

Let's do the same computation with NumPy. First we will get the NumPy array from the ironArray one:

and now the actual reduction:

In [29]:
%%mprof_run 5.numpy::median_memory
np_reduc = np.median(precip, axis=(3, 0))

memprofiler: used -3991.34 MiB RAM (peak of 4507.75 MiB) in 73.3930 s, total RAM usage 41.33 MiB


In [30]:
np.testing.assert_allclose(ia_reduc, np_reduc, atol=1e-5, rtol=1e-5)
del np_reduc

### Zarr

In [31]:
%%mprof_run 2.zarr::median_memory
zdask_reduc = da.median(precip_zdask, axis=(3, 0))
zarr_reduc = zarr.create(shape=ia_reduc.shape, dtype=ia_reduc.dtype)
da.to_zarr(zdask_reduc, zarr_reduc)

memprofiler: used 1079.38 MiB RAM (peak of 8952.28 MiB) in 11.8600 s, total RAM usage 1227.19 MiB


In [32]:
np.testing.assert_almost_equal(zarr_reduc, ia_reduc)
del zdask_reduc
del zarr_reduc

### HDF5

In [33]:
%%mprof_run 3.hdf5::median_memory

h5dask_reduc = da.median(precip_h5dask, axis=(3, 0))

f = h5py.File(h5_reduc_urlpath, "w", driver='core', backing_store=False)
h5_reduc = f.create_dataset(name=h5_reduc_urlpath, shape=ia_reduc.shape, dtype=ia_reduc.dtype, **h5plugin.Blosc())
da.to_hdf5(h5_reduc_urlpath, '/x', h5dask_reduc)
f.close()

memprofiler: used 609.34 MiB RAM (peak of 7078.74 MiB) in 26.9696 s, total RAM usage 1844.65 MiB


In [34]:
del h5dask_reduc
del h5_reduc

### TileDB

In [35]:
%%mprof_run 4.tiledb::median_memory
res_dask_opt = da.median(dask_tiledb, axis=(3, 0))
res_dask_opt.to_tiledb("mem://res_tiledb")

NameError: name 'dask_tiledb' is not defined

memprofiler: used 0.31 MiB RAM (peak of 0.31 MiB) in 0.1919 s, total RAM usage 1933.43 MiB


In [36]:
del res_dask_opt
del dask_tiledb
tiledb.remove("mem://res_tiledb")

NameError: name 'res_dask_opt' is not defined

### Results

Finally, we will do a plot of the memory and time consumption with each different library.

In [ ]:
%mprof_plot .*::median